# HuggingFace Transformers를 이용한 NLI 모델 학습

* 본 노트북에서는 klue/roberta-base 모델을 kakaobrain에서 제공하는 KorNLI 데이터셋을 활용하여 모델을 훈련하는 예제입니다. 

* KorNLI 데이터셋은 [kakaobrain](https://github.com/kakaobrain/KorNLUDatasets?fbclid=IwAR0LX_jem7qb6HUikflO-F6lPpfoefK9Yc0jSQIdSKdkX4s8SW1UvoVGc7I)에서 제공하는 데이터셋이며, KLUE의 NLI 데이터셋 보다 데이터 크기가 더 커서 시간이 오래 걸립니다. 

* 모든 소스 코드는 [huggingface-notebook](https://github.com/huggingface/notebooks)을 참고하였습니다.

* 본 노트북의 학습 내용 대부분은 Huffon님의 [klue-transformers-tutorial](https://github.com/Huffon/klue-transformers-tutorial)을 참고하였습니다.

* 학습을 통해 얻어질 klue-roberta-base-kornli 모델은 입력된 두 문장의 추론 관계를 예측하는데 사용할 수 있게 됩니다.

* 노트북의 환경은 ainize workspace 입니다. [ainze](https://ainize.ai/) 홈페이지 오른쪽 상단의 github로 아이디 생성 후 My space에서 workspace를 생성할 수 있습니다. 제가 사용한 workspace의 GPU 환경은 tesla V100 32GB입니다.


## 노트북 환경 설정

모델을 학습시키기 전에 자신의 노트북 환경을 확인하고 필요한 라이브러리를 설치합니다.

In [1]:
import torch
use_cuda = torch.cuda.is_available()
print(use_cuda)

True


모델을 학습시킬 때 GPU를 사용해야 학습을 빠르게 할 수 있으므로 학습시키기 전 자신의 노트북 환경에서 GPU가 잘 동작 하는지 확인을 합니다. True가 출력이 된다면 학습할 때 GPU가 동작하는 것이고 False가 나오면 동작하지 않는 것입니다. False가 출력이 되신다면 검색을 통해 GPU를 활성화 시키는 방법을 찾아 활성화 시키시면 됩니다.

In [2]:
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 4073418392972710111
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 19146211328
locality {
  bus_id: 1
  links {
  }
}
incarnation: 16025480191014330435
physical_device_desc: "device: 0, name: Tesla V100-DGXS-32GB, pci bus id: 0000:07:00.0, compute capability: 7.0"
]


본인이 작성하고 있는 노트북 GPU 환경을 알 수 있는 코드입니다. 저는 ainize workspace에서 Tesla V100 환경에서 노트북을 테스트했기 때문에 Tesla V100-DGXS-32GB이라고 잘 나오네요.

In [3]:
#!pip install -U transformers datasets scipy scikit-learn

모델 훈련을 위한 transformers와 학습 데이터셋 로드를 위해 datasets 라이브러리를 설치합니다. 그 외 모델 성능 검증을 위해 scipy, scikit-learn 또한 추가로 설치해줍니다.


## 문장 분류 모델 학습

In [4]:
import random
import logging
import torch
from IPython.display import display, HTML
import numpy as np
import pandas as pd
import datasets
from datasets import load_dataset, load_metric, ClassLabel, Sequence, list_datasets
from transformers import AutoTokenizer, AutoModelForSequenceClassification, TrainingArguments, Trainer


노트북을 실행하는데 필요한 라이브러리를 모두 임포트 해줍니다.

In [5]:
model_checkpoint = "klue/roberta-base"
batch_size = 32
task = "nli"

학습에 필요한 정보를 변수로 기록합니다.

본 노트북애서는 klue-roberta-base 모델을 활용하지만, https://huggingface.co/klue 페이지에서 더 다양한 사전학습 언어 모델을 확인하실 수 있습니다.

학습 태스크로는 nli를, 배치 사이즈는 32로 지정하겠습니다.

In [6]:
datasets = load_dataset("kor_nlu", task)

Reusing dataset kor_nlu (/workspace/.cache/huggingface/datasets/kor_nlu/nli/1.0.0/4facbba77df60b0658056ced2052633e681a50187b9428bd5752ebd59d332ba8)


저는 학습에 사용할 데이터셋을 kakaobrain에서 제공하는 KorNLI 데이터셋을 사용할 것이므로 HuggingFace datasets 라이브러리에 등록된 kor_nlu의 nli 데이터을 다운로드 합니다.

In [7]:
datasets

DatasetDict({
    train: Dataset({
        features: ['premise', 'hypothesis', 'label'],
        num_rows: 550146
    })
    validation: Dataset({
        features: ['premise', 'hypothesis', 'label'],
        num_rows: 1570
    })
    test: Dataset({
        features: ['premise', 'hypothesis', 'label'],
        num_rows: 4954
    })
})

다운로드 후 얻어진 datasets의 객체를 보면 KorNLI 데이터에는 훈련 데이터, 검증 데이터, 테스트 데이터가 포함되어 있는 것을 확인할 수 있습니다.

In [8]:
datasets["train"][0]

{'premise': '말을 탄 사람이 고장난 비행기 위로 뛰어오른다.',
 'hypothesis': '한 사람이 경쟁을 위해 말을 훈련시키고 있다.',
 'label': 1}

각 데이터는 위와 같이 두개의 문장과 두 문장의 추론 관계를 라벨로 가지고 있습니다.

In [9]:
def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."

    picks = []
    
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)

        # 이미 등록된 예제가 뽑힌 경우, 다시 추출
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)

        picks.append(pick)

    # 임의로 추출된 인덱스들로 구성된 데이터 프레임 선언
    df = pd.DataFrame(dataset[picks])

    for column, typ in dataset.features.items():
        # 라벨 클래스를 스트링으로 변환
        if isinstance(typ, ClassLabel):
            df[column] = df[column].transform(lambda i: typ.names[i])

    display(HTML(df.to_html()))

데이터셋을 전반적으로 살펴보기 위해 시각화 함수를 정의합니다.

In [10]:
show_random_elements(datasets["train"])

앞서 정의한 함수를 이용하여 임의의 훈련 데이터를 살펴보도록 합니다.

KorNLI에는 관계 추론을 할 때 entailment, neutral 그리고 contradiction 세 개의 라벨을 가지고 있음을 알 수 있습니다.

이렇게 데이터를 살펴보면 각 라벨에 어떠한 문장들이 해당되는지 알 수 있어 감을 익힐 수 있는데에 장점이 있습니다.

In [11]:
metric = load_metric("glue", "qnli")

훈련 과정 중 모델의 성능 파악을 위해 메트릭을 설정합니다.

datasets 라이브러리에는 이미 구현된 메트릭을 사용할 수 있는 load_metric 함수가 있어서 쉽게 설정이 가능합니다.

그 중 GLUE 데이터셋의 qnli 태스크의 메트릭을 사용하도록 하겠습니다.

In [12]:
fake_preds = np.random.randint(0, 2, size=(64,))
fake_labels = np.random.randint(0, 2, size=(64,))
fake_preds, fake_labels

(array([0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1,
        0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1,
        1, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1, 1, 0, 0]),
 array([0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0,
        1, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0, 1, 1]))

메트릭이 정상적으로 작동하는 것을 확인하기 위해 랜덤한 예측 값과 라벨 값을 생성합니다.

In [13]:
metric.compute(predictions=fake_preds, references=fake_labels)

{'accuracy': 0.5}

생성한 랜덤 값들을 compute() 함수를 통해 잘 동작하는지 확인합니다.

In [14]:
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint, use_fast=True)

이제 학습에 활용할 토크나이저를 로드해옵니다.

In [15]:
tokenizer("한 사람이 경쟁을 위해 말을 훈련시키고 있다.", "말을 탄 사람이 고장난 비행기 위로 뛰어오른다.")

{'input_ids': [0, 1891, 3611, 2052, 3855, 2069, 3627, 1041, 2069, 4484, 2067, 2089, 2088, 1513, 2062, 18, 2, 1041, 2069, 1763, 3611, 2052, 8514, 2336, 7046, 7587, 5603, 17290, 2062, 18, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1], 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]}

로드된 토크나이저가 두 문장을 토큰화하는 방식을 파악하기 위해 두 문장을 입력 값으로 넣어서 확인해 봅니다.

In [16]:
sentence1_key, sentence2_key = ("premise", "hypothesis")
print(f"Sentence 1: {datasets['train'][0][sentence1_key]}")
print(f"Sentence 2: {datasets['train'][0][sentence2_key]}")

Sentence 1: 말을 탄 사람이 고장난 비행기 위로 뛰어오른다.
Sentence 2: 한 사람이 경쟁을 위해 말을 훈련시키고 있다.


이제 앞서 로드한 데이터셋에서 각 문장에 해당하는 value를 뽑아주기 위한 key를 정의합니다.

KorNLI 데이터셋에서 두 문장의 label이 각각 premise와 hypothesis라는 이름으로 정의된 것을 확인하였으므로, 두 문장의 key 는 마찬가지로 각각 premise, hypothesis가 됩니다.

In [20]:
def preprocess_function(examples):
    print(examples)
    return tokenizer(
        examples[sentence1_key],
        examples[sentence2_key],
        truncation=True,
        return_token_type_ids=False,
    )

이제 key 도 확인이 되었으니, 데이터셋에서 각 예제들을 뽑아와 토큰화 할 수 있는 함수를 위와 같이 정의해줍니다.

해당 함수는 모델을 훈련하기 앞서 데이터셋을 미리 토큰화 시켜놓는 작업을 위한 콜백 함수로 사용되게 됩니다.

인자로 넣어주는 truncation는 모델이 입력 받을 수 있는 최대 길이 이상의 토큰 시퀀스가 들어오게 될 경우, 최대 길이 기준으로 시퀀스를 자르라는 의미를 지닙니다.

( * return_token_type_ids는 토크나이저가 token_type_ids를 반환하도록 할 것인지를 결정하는 인자입니다. transformers==4.7.0 기준으로 token_type_ids가 기본적으로 반환되므로 token_type_ids 자체를 사용하지 않는 RoBERTa 모델을 활용하기 위해 해당 인자를 False로 설정해주도록 합니다.)

In [21]:
preprocess_function(datasets["train"][:40])

{'premise': ['말을 탄 사람이 고장난 비행기 위로 뛰어오른다.', '말을 탄 사람이 고장난 비행기 위로 뛰어오른다.', '말을 탄 사람이 고장난 비행기 위로 뛰어오른다.', '카메라에 웃고 손을 흔드는 아이들', '카메라에 웃고 손을 흔드는 아이들', '카메라에 웃고 손을 흔드는 아이들', '한 소년이 빨간 다리 한가운데 스케이트보드에 뛰어오르고 있다.', '한 소년이 빨간 다리 한가운데 스케이트보드에 뛰어오르고 있다.', '한 소년이 빨간 다리 한가운데 스케이트보드에 뛰어오르고 있다.', '나이 든 남자가 커피숍의 작은 테이블에 오렌지 주스를 들고 앉아 있고 밝은 색 셔츠를 입은 직원들은 뒤에서 미소를 짓고 있다.', '나이 든 남자가 커피숍의 작은 테이블에 오렌지 주스를 들고 앉아 있고 밝은 색 셔츠를 입은 직원들은 뒤에서 미소를 짓고 있다.', '나이 든 남자가 커피숍의 작은 테이블에 오렌지 주스를 들고 앉아 있고 밝은 색 셔츠를 입은 직원들은 뒤에서 미소를 짓고 있다.', '금발 여자 둘이 서로 껴안고 있다.', '금발 여자 둘이 서로 껴안고 있다.', '금발 여자 둘이 서로 껴안고 있다.', '식당에 있는 몇몇 사람들, 그들 중 한 명은 오렌지 주스를 마시고 있다.', '식당에 있는 몇몇 사람들, 그들 중 한 명은 오렌지 주스를 마시고 있다.', '식당에 있는 몇몇 사람들, 그들 중 한 명은 오렌지 주스를 마시고 있다.', '한 나이든 남자가 식당에서 오렌지 주스를 마시고 있다.', '한 나이든 남자가 식당에서 오렌지 주스를 마시고 있다.', '한 나이든 남자가 식당에서 오렌지 주스를 마시고 있다.', '금발의 남자, 그리고 공공 분수대에서 술을 마시는 갈색 셔츠.', '금발의 남자, 그리고 공공 분수대에서 술을 마시는 갈색 셔츠.', '금발의 남자, 그리고 공공 분수대에서 술을 마시는 갈색 셔츠.', '방금 점심을 먹고 작별인사를 한 두 여자.', '방금 점심을 먹고 작별인사를 한 두 여자.', '방금 점심을 먹고 작별인사를 한 두 여자.

{'input_ids': [[0, 1041, 2069, 1763, 3611, 2052, 8514, 2336, 7046, 7587, 5603, 17290, 2062, 18, 2, 1891, 3611, 2052, 3855, 2069, 3627, 1041, 2069, 4484, 2067, 2089, 2088, 1513, 2062, 18, 2], [0, 1041, 2069, 1763, 3611, 2052, 8514, 2336, 7046, 7587, 5603, 17290, 2062, 18, 2, 1891, 3611, 2052, 5499, 27135, 3, 4867, 19521, 1513, 2062, 18, 2], [0, 1041, 2069, 1763, 3611, 2052, 8514, 2336, 7046, 7587, 5603, 17290, 2062, 18, 2, 3611, 2073, 8296, 27135, 1041, 2069, 11532, 1513, 2062, 18, 2], [0, 5677, 2170, 1474, 2088, 1284, 2069, 18882, 2259, 3651, 2031, 2, 636, 2031, 2073, 4267, 2098, 2069, 4530, 1474, 2088, 1513, 2062, 2], [0, 5677, 2170, 1474, 2088, 1284, 2069, 18882, 2259, 3651, 2031, 2, 3651, 7285, 1513, 2062, 2], [0, 5677, 2170, 1474, 2088, 1284, 2069, 18882, 2259, 3651, 2031, 2, 3651, 7285, 3977, 2069, 19556, 2088, 1513, 2062, 2], [0, 1891, 5950, 2052, 8013, 5035, 6853, 3832, 19090, 11507, 2170, 5603, 5667, 2088, 1513, 2062, 18, 2, 5950, 2073, 4543, 2138, 3653, 19090, 2138, 25695, 18,

앞서 정의한 process_function은 위와 같이 여러 개의 예제 데이터를 받을 수도 있습니다.

In [ ]:
encoded_datasets = datasets.map(preprocess_function, batched=True)

이제 정의된 전처리 함수를 활용해 데이터셋을 미리 토큰화시키는 작업을 수행합니다.

datasets 라이브러리를 통해 얻어진 DatasetDict 객체는 map() 함수를 지원하므로, 정의된 전처리 함수를 데이터셋 토큰화를 위한 콜백 함수로 map() 함수 인자로 넘겨주면 됩니다.

In [ ]:
num_labels = 3
model = AutoModelForSequenceClassification.from_pretrained(model_checkpoint, num_labels=num_labels)

학습을 위한 모델을 로드합니다.

앞서 살펴본 바와 같이 KorNLI에는 총 3개의 클래스가 존재하므로, 3개의 클래스를 예측할 수 있는 SequenceClassification 구조로 모델을 로드합니다.

모델을 로드할 때 발생하는 경고 문구는 두 가지 의미를 지닙니다.
1. Masked Language Modeling 을 위해 존재했던 lm_head가 현재는 사용되지 않고 있음을 의미합니다.
2. 문장 분류를 위한 classifier 레이어를 백본 모델 뒤에 이어 붙였으나 아직 훈련이 되지 않았으므로, 학습을 수행해야 함을 의미합니다.

In [ ]:
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return metric.compute(predictions=predictions, references=labels)

마지막으로 앞서 정의한 메트릭을 모델 예측 결과에 적용하기 위한 함수를 정의합니다.

입력으로 들어오는 eval_pred는 EvalPrediction 객체이며, 모델의 클래스 별 예측 값과 정답 값을 지닙니다.

클래스 별 예측 중 가장 높은 라벨을 argmax()를 통해 뽑아낸 후, 정답 라벨과 비교를 하게 됩니다.

In [ ]:
metric_name = "accuracy"

args = TrainingArguments(
    "test-nli",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=5,
    weight_decay=0.01,
    load_best_model_at_end=True,
    metric_for_best_model=metric_name,
)

이제 앞서 정의한 정보들을 바탕으로 transformers에서 제공하는 Trainer 객체를 활용하기 위한 인자 관리 클래스를 초기화합니다.

metric_name은 앞서 얻어진 메트릭 함수를 활용했을 때, 아래와 같이 dict 형식으로 결과 값이 반환되는데 여기서 우리가 사용할 key 를 정의해준다고 생각하시면 됩니다.


In [ ]:
trainer = Trainer(
    model,
    args,
    train_dataset=encoded_datasets["train"],
    eval_dataset=encoded_datasets["validation"],
    tokenizer=tokenizer,
    compute_metrics=compute_metrics,
)

이제 로드한 모델, 인자 관리 클래스, 데이터셋 등을 이용하여 Trainer를 초기화 해줍니다.

In [ ]:
trainer.train()

앞서 초기화한 trainer 객체를 훈련시킵니다. 데이터 셋의 크기가 커서 그런지 제 환경에서는 약 3시간 30분 정도 걸렸네요.

In [ ]:
trainer.evaluate()

학습한 모델을 evalutate()를 통해 평가를 하여 정확도를 확인해 봅니다.

In [ ]:
trainer.save_model("./")

학습한 모델을 나중에 사용하기 위해 저장 경로에 저장합니다. 저는 현재 폴더에 저장하였습니다.

## 마치며

제가 인공지능을 시작한지 얼마 되지 않아 개념이 덜 잡혀있고, 정말 어려워 했었는데 Huffon님의 [github](https://github.com/Huffon)에 올라가있는 노트북을 보며 많이 배운 것 같습니다. 본 노트북은 Huffon님의 예제 코드와 설명을 따라친 것이 대부분이지만 눈으로 보는 것과 실제 해보는 것의 차이가 엄청 크다는 것을 느꼈습니다.